# Folium - Mapas de coropletas

## Importación de módulos de Python

In [1]:
import folium
import pandas as pd

import json

In [2]:
# Impresión de la versión de Folium
print(folium.__version__)

0.11.0


In [3]:
# Impresión de la versión de Pandas
print(pd.__version__)

1.1.3


## Clase [Choropleth](https://python-visualization.github.io/folium/modules.html#folium.features.Choropleth)

Esta clase de Folium crea un [mapa de coropletas](https://en.wikipedia.org/wiki/Choropleth_map) y lo colorea de acuerdo al valor de un campo de datos.

El método constructor de Choropleth recibe como parámetros la ubicación de los datos geoespaciales en formato GeoJSON (ej. en un archivo) y puede recibir también un conjunto de datos tabulares en un dataframe de [pandas](https://pandas.pydata.org/). Otros parámetros se utilizan para especificar los campos de datos según los que se colorea el mapa, así como los campos que se utilizan para enlazar los datos espaciales y tabulares.

En el siguiente ejemplo, se crea un mapa de coropletas que refleja la cantidad de casos positivos de COVID-19 en los cantones de Costa Rica, de acuerdo con los [datos publicados por el Ministerio de Salud](http://geovision.uned.ac.cr/oges/). El archivo GeoJSON de cantones proviene de la capa publicada por el Instituto Geográfico Nacional (IGN) en el [Sistema Nacional de Información Territorial (SNIT)](https://www.snitcr.go.cr/).

La función [read_csv()](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.read_csv.html) carga un archivo CSV en un [dataframe](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.html) de pandas.

In [4]:
# Carga de datos tabulares de casos positivos de COVID-19 en un dataframe
df_positivos = pd.read_csv('datos/10_07_CSV_POSITIVOS_ULTIMA_FECHA.csv', sep=',')

In [5]:
df_positivos

Unnamed: 0  cod_canton  positivos
0            1         112        490
1            2         110       3943
2            3         106       1149
3            4         118       2078
4            5         103       6111
..         ...         ...        ...
78          79         705        389
79          80         702       1234
80          81         703        830
81          82         704        602
82          83         999        532

[83 rows x 3 columns]

La función [rename()](https://pandas.pydata.org/pandas-docs/version/0.23.4/generated/pandas.DataFrame.rename.html) renombra una columna de un dataframe.

In [6]:
# Renombramiento de la primera columna
df_positivos.rename(columns = {'Unnamed: 0': 'id'}, inplace=True)

La función [head()](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.head.html) despliega las primeras filas de un dataframe.

In [7]:
# Despliegue de las primeras filas, para observación de los datos
df_positivos.tail(10)

id  cod_canton  positivos
73  74         609        126
74  75         601       2017
75  76         606        328
76  77         706        440
77  78         701       1843
78  79         705        389
79  80         702       1234
80  81         703        830
81  82         704        602
82  83         999        532

In [8]:
# GeoJSON de cantones
# geo_cantones = r'datos/cr_cantones_wgs84.geojson'
geo_cantones = r'datos/cr_limite_cantonal_ign_wgs84.geojson'

# Mapa base
m = folium.Map(
    location=[10, -84], 
    zoom_start=7, 
    tiles='openstreetmap')


# Capa de coropletas coloreada de acuerdo con el campo de casos positivos.
# El enlace entre los datos geoespaciales y tabulares se realiza a través del campo "cod_canton" del dataframe
# y el campo del mismo nombre en el archivo GeoJSON.
m.choropleth(
    geo_data=geo_cantones,
    data=df_positivos,
    columns=['cod_canton', 'positivos'],
    bins=8,
    key_on='feature.properties.cod_canton',
    fill_color='Reds', 
    fill_opacity=1, 
    line_opacity=1,
    legend_name='Casos positivos',
    smooth_factor=0)


# Despliegue del mapa
m

C:\Users\mfvargas\anaconda3\envs\leccion-10\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [9]:
m.save('index.html')

### Ventana emergente con datos de un polígono

In [10]:
# GeoJSON de cantones
geo_cantones = r'datos/cr_limite_cantonal_ign_wgs84.geojson'

# Mapa base
m = folium.Map(
    location=[10, -84], 
    zoom_start=7, 
    tiles='openstreetmap')

# Capa de coropletas coloreada de acuerdo con el campo de casos positivos.
choropleth = folium.Choropleth(
    geo_data=geo_cantones,
    data=df_positivos,
    columns=['cod_canton', 'positivos'],
    bins=8,
    key_on='feature.properties.cod_canton',
    fill_color='Reds', 
    fill_opacity=1, 
    line_opacity=1,
    legend_name='Casos positivos',
    name='Casos positivos',
    smooth_factor=0).add_to(m)

In [11]:
# Se crea un campo adicional en la estructura de la capa GeoJSON para almacenar el texto de la ventana emergente
for feature in choropleth.geojson.data['features']:
    # print(type(feature['properties']))
    canton_filtrado_df = df_positivos[df_positivos['cod_canton'] == feature['properties']['cod_canton']]
    feature['properties']['texto_emergente'] = feature['properties']['canton'] + "<br>" + str(canton_filtrado_df.iloc[0]['positivos'])

# Se especifica el nuevo campo como el contenido de la ventana emergente
choropleth.geojson.add_child(folium.features.GeoJsonTooltip(['texto_emergente'], labels=False))

# Otra opción para explorar
# choropleth.add_child(folium.Popup('Texto emergente'))

# Despliegue del mapa
m    